# Testing SOM + Geospatial Visualization

## Setup

In [1]:
import os
import re
import sys
import sqlite3
import pandas as pd
import numpy as np
import ipywidgets 
from tqdm.notebook import trange, tqdm
import time
import datetime
import warnings
warnings.filterwarnings("ignore")

import logging
from scipy.stats import linregress


from sklearn.preprocessing import StandardScaler



from itertools import combinations, permutations


import json

from bokeh.models import GeoJSONDataSource
from bokeh.plotting import figure, show
from bokeh.sampledata.sample_geojson import geojson

from bokeh.models import LogColorMapper
from bokeh.palettes import Viridis6 as palette
from bokeh.plotting import figure, show
from bokeh.palettes import interp_palette


from bokeh.io import output_notebook, push_notebook, show

from bokeh.models import LogColorMapper
from bokeh.palettes import Viridis6 as palette
from bokeh.plotting import figure, show
from bokeh.models import ColorBar, HoverTool, BasicTicker



from bokeh.plotting import figure, output_file, show
from bokeh.layouts import column, row, gridplot, layout
from bokeh.palettes import Set3, Spectral

from bokeh.io import curdoc, show, output_notebook

from bokeh.models import ColumnDataSource, CDSView, CustomJS
from bokeh.models import DataTable, DateFormatter, TableColumn

from bokeh.models import Grid, HexTile, LinearAxis, Div, Plot, Scatter, Select
from bokeh.models import LinearColorMapper, ColorBar, LabelSet, HoverTool

from bokeh.models import AllIndices, GroupFilter, IndexFilter, FactorRange

from bokeh.transform import linear_cmap, factor_cmap
from bokeh.palettes import viridis
from bokeh.util.hex import axial_to_cartesian, cartesian_to_axial

from bokeh.models import ColumnDataSource, Whisker
from bokeh.plotting import figure, show
from bokeh.transform import factor_cmap, jitter

from bokeh.models import ColumnDataSource, Whisker
from bokeh.plotting import figure, show
from bokeh.transform import factor_cmap, jitter

from bokeh.io import show
from bokeh.models import CheckboxButtonGroup, CustomJS


# import colorcet as cc

from bokeh.models import ColumnDataSource, Whisker
from bokeh.plotting import figure, show
from bokeh.sampledata.autompg2 import autompg2 as df_mpg
from bokeh.transform import factor_cmap, jitter


%matplotlib inline
import matplotlib.pyplot as plt
import matplotlib as mpl
import pandas as pd
import geopandas

import os

from bokeh.plotting import figure, output_file, show, save,output_notebook
from bokeh.models import GeoJSONDataSource, LinearColorMapper, ColorBar
from bokeh.models import Slope
from bokeh.models import CustomJS, RadioButtonGroup

from bokeh.palettes import brewer

from scipy import stats
import json

import umap

import matplotlib.pyplot as plt
import seaborn as sns
import matplotlib.colors as mpl_colors
output_notebook()



Loading BokehJS ...

In [2]:
if os.path.abspath('..') not in sys.path:
    sys.path.append(os.path.join(os.path.abspath('..')))
    
    print('parent not in path, appending')
    
if os.path.abspath('.') not in sys.path:
    sys.path.append(os.path.join(os.path.abspath('.')))
    
    print('parent not in path, appending')
    

parent not in path, appending
parent not in path, appending


In [3]:
from minisom import MiniSom

In [4]:
from bokeh.io import output_file, output_notebook, show
from bokeh.plotting import figure, ColumnDataSource

from bokeh.models import (
    Range1d,
    GeoJSONDataSource,
    HoverTool,
    LinearColorMapper,
    GMapPlot, GMapOptions, ColumnDataSource, 
    Circle, DataRange1d, PanTool, WheelZoomTool, BoxSelectTool
)

In [5]:
import libpysal as ps

import geopandas as gp

from geodatasets import get_path

from mgwr.gwr import GWR, MGWR
from mgwr.sel_bw import Sel_BW
from mgwr.utils import shift_colormap, truncate_colormap


from esda.moran import Moran_BV, Moran_Local_BV
from splot.esda import moran_scatterplot


from pysal.explore import esda
from pysal.lib import weights as pysal_weights

## Geopandas to GeoJSONDataSource

In [6]:
geo_df = gp.read_file('./georgia/G_utm.shp')
geo_df

AREA  PERIMETER  G_UTM_  G_UTM_ID             AREANAME  Latitude  \
0    9.786480e+08   174967.0       2         1     GA, Rabun County  34.88129   
1    4.461530e+08   115140.0       3         2     GA, Towns County  34.91864   
2    8.543330e+08   160360.0       4         7     GA, Union County  34.83436   
3    1.014270e+09   179577.0       5         4    GA, Fannin County  34.86415   
4    8.980900e+08   183295.0       6         3    GA, Murray County  34.78193   
..            ...        ...     ...       ...                  ...       ...   
167  1.617320e+09   175599.0     171       166   GA, Decatur County  30.87876   
168  6.657950e+08   128639.0     172       171  GA, Seminole County  30.93315   
169  1.325180e+09   202475.0     173       172   GA, Lowndes County  30.83468   
170  1.093810e+09   155814.0     174       173    GA, Echols County  30.71670   
171  1.404320e+06     6761.5     175       174    GA, Brooks County  30.84653   

     Longitud  TotPop90  PctRural  PctBach  PctEld  PctFB  PctPov  PctBlack  \
0   -83.40143     11648     100.0     11.6   17.18   1.13    13.6      0.35   
1   -83.73908      6754     100.0     11.4   22.96   1.36    14.0      0.00   
2   -83.99088     11993     100.0     10.1   17.55   0.88    18.3      0.10   
3   -84.31928     15992     100.0      7.8   17.30   0.58    17.2      0.03   
4   -84.74823     26147      89.0      5.5    7.69   0.50    11.3      0.26   
..        ...       ...       ...      ...     ...    ...     ...       ...   
167 -84.57963     25511      58.0     11.7   13.02   1.54    23.3     39.47   
168 -84.86705      9010      69.4      7.8   14.20   5.69    29.1     32.74   
169 -83.26782     75981      47.6     16.3    8.99   1.53    19.9     31.88   
170 -82.89896      2334     100.0      4.7    9.77   1.63    14.6     11.48   
171 -83.57726     15398      65.6      9.1   13.68   1.76    25.9     41.47   

            X        Y  AreaKey  \
0    824645.5  3864805    13241   
1    797981.7  3872640    13281   
2    777040.1  3858779    13291   
3    739255.8  3866604    13111   
4    707834.3  3854188    13213   
..        ...      ...      ...   
167  732628.4  3421800    13087   
168  704495.6  3422002    13253   
169  864781.1  3419313    13185   
170  896654.0  3401148    13101   
171  827822.0  3421638    13027   

                                              geometry  
0    POLYGON ((806227.188 3858275.500, 805577.812 3...  
1    POLYGON ((779645.188 3875727.750, 808540.188 3...  
2    POLYGON ((762005.000 3875204.000, 773345.688 3...  
3    POLYGON ((717121.188 3874113.750, 744454.625 3...  
4    POLYGON ((699833.188 3873629.500, 703008.812 3...  
..                                                 ...  
167  POLYGON ((737720.625 3440711.000, 750335.938 3...  
168  POLYGON ((716518.562 3439257.750, 716485.625 3...  
169  POLYGON ((863028.062 3438358.250, 864649.812 3...  
170  POLYGON ((880751.438 3419449.750, 881138.125 3...  
171  POLYGON ((850741.562 3394746.750, 851109.812 3...  

[172 rows x 18 columns]

In [7]:
geo_df_columns = geo_df.columns

In [8]:
geo_df.columns

Index(['AREA', 'PERIMETER', 'G_UTM_', 'G_UTM_ID', 'AREANAME', 'Latitude',
       'Longitud', 'TotPop90', 'PctRural', 'PctBach', 'PctEld', 'PctFB',
       'PctPov', 'PctBlack', 'X', 'Y', 'AreaKey', 'geometry'],
      dtype='object')

In [9]:
geo_df['_DF_ID'] = geo_df.index.copy()
## Code from mgwr docs
# Load Georgia dataset and generate plot of Georgia counties (Figure 1)

# gp_georgia = gp.read_file(ps.examples.get_path('G_utm.shp'))
# georgia_data_feats = ['TotPop90', 'PctRural', 'PctBach', 'PctEld', 'PctFB', 'PctPov', 'PctBlack']


In [10]:
# lisbon_shp_path = "./assets/SOM/project3/project3data.shp"

In [11]:
# https://stackoverflow.com/questions/57027969/bokeh-plots-an-empty-map-from-a-shapefile-converted-to-geojson-and-dont-know-wh

# LX_LAYER = geopandas.read_file(lisbon_shp_path)
# LX_LAYER.head()


In [12]:
# LX_LAYER.describe()

## Preprocess numeric data

In [13]:
features = ['TotPop90', 
            'PctRural', 'PctBach', 'PctEld', 'PctFB', 'PctPov', 'PctBlack']
geo_features = ['X', 'Y']


In [14]:
feats = {
    'all' : features,
    'geo' : { 'x' : 'X', 'y': 'Y'},
    'suf' : {
        'scaled' : '_std'
    }
}



In [15]:
gp_df = geo_df.copy()


In [16]:
features_scaled = ["{}{}".format(i, feats['suf']['scaled']) for i in features]
st_scaler = StandardScaler()

gp_df[features_scaled] = st_scaler.fit_transform(gp_df[features])

In [17]:
gp_df_orig = gp_df.copy()

## Get text details

In [18]:
details = {}

## SOM

### Train SOM

In [19]:
som_params = {
    "epochs" : 3000,
    "random_state": 0,
    "learning_rate": 0.7,
    "initialization": 'random',
    "m": 9,
    "n": 12,
}


p_ = len(features)
mn = (som_params['m'], som_params['n'])

def inverse_decay_to_zero(learning_rate, t, max_iter):
    """Decay function of the learning process that asymptotically
    approaches zero.
    """
    C = max_iter / 100.0
    return learning_rate * C / (C + t)

def inverse_decay_to_one(learning_rate, t, max_iter):
        """Decay function of sigma that asymptotically approaches one.
        """
        C = (learning_rate - 1) / max_iter
        return learning_rate / (1 + (t * C))

sigma_ = int(min(mn))


som_gp = MiniSom(som_params['m'], 
                 som_params['n'], 
                 p_, 
                 sigma=sigma_, 
                 learning_rate=som_params['learning_rate'], 
                 activation_distance='euclidean',
                 topology='hexagonal', 
                 neighborhood_function='gaussian',
                 decay_function=inverse_decay_to_zero,
                 # decay_function=inverse_decay_to_one,
                 random_seed=som_params['random_state'],

                )

gp_vals = gp_df[features_scaled].values
som_gp.train(gp_vals, 
             som_params['epochs'],
             use_epochs=True,
             verbose=True
             )
qe = som_gp.quantization_error(gp_vals)
te = som_gp.topographic_error(gp_vals)


print(qe, te)



def get_row_bmu(row, som, mn):
    """
    Returns the longform ID of the BMU for this row
    """
    row_ = row.values
    return np.ravel_multi_index(som.winner(row.values),mn)

gp_df['BMU'] = gp_df[features_scaled].apply(lambda row: get_row_bmu(row, som_gp, mn) , axis=1)


 [ 516000 / 516000 ] 100% - 0:00:00 left 
 quantization error: 0.43493817455111183
0.43493817455111183 0.2093023255813954


### Test: Visualize SOM

In [20]:
# PLOT_WIDTH = 400
# PLOT_HEIGHT = 700
# CONTRAST_COLOR1 = "#ff6361"
# CONTRAST_COLOR2 = "#bc5090"
# m=som_params['m']
# n=som_params['n']

# xx, yy = som_gp.get_euclidean_coordinates()

# weights = som_gp.get_weights()

# umatrix = som_gp.distance_map(scaling='mean')
# umatrix_vals = umatrix.reshape(m*n)
# c = umatrix.reshape(m*n)


# hitsmatrix = som_gp.activation_response(gp_df[features_scaled].values)
    

# hits_flat = hitsmatrix.reshape(m*n)
# umat_flat = umatrix.reshape(m*n)

# hits_pct = hitsmatrix.reshape(m*n) / hitsmatrix.max()

# # hits_labels = [ i.astype(int).astype(str) if i > 0 else '' for i in c2 ]
# # hits_labels_color = [ 1 if i.astype(int) > (.75*np.mean([max(c2), min(c2)])) else 0 for i in c2 ] 

# palette = 'Viridis256'

# umatrix_cmap = LinearColorMapper(palette=palette,
#                             low = 0, 
#                             high = max(c))

In [77]:
som_cp = {}
for i in range(len(features_scaled)):
    som_df[features[i]] = som_gp.get_weights()[:,:,i].reshape(m*n)

som_cp

{}

In [82]:
hits_pct = hitsmatrix.reshape(m*n) / hitsmatrix.max()
hits_pct

array([1. , 0.4, 0.4, 0.8, 0.4, 0.8, 0.6, 0.4, 0.4, 0.2, 0.4, 0.8, 0.4,
       0.4, 0. , 0.4, 0.2, 0.2, 0.2, 0.6, 0. , 0. , 0.2, 0.2, 0.8, 0.2,
       0.2, 0.6, 0.6, 0.2, 0.2, 0.2, 0.4, 0.4, 0.2, 0.4, 0.4, 0.8, 0.4,
       0. , 0.4, 0.2, 0.2, 0.6, 0.2, 0. , 0.4, 0.4, 0.2, 0. , 0.4, 0.6,
       0.2, 0.4, 0.4, 0.2, 0.4, 0.4, 0.4, 0.2, 0.4, 0. , 0.2, 0.4, 0. ,
       0.4, 0. , 0.4, 0.2, 0.2, 0.2, 0.6, 0.8, 0.2, 0.4, 0.4, 0. , 0.6,
       0.2, 0.2, 0.6, 0.4, 0.4, 0.2, 0. , 0. , 0.2, 0.2, 0. , 0.4, 0. ,
       0.2, 0. , 0. , 0. , 0.4, 0.4, 0.4, 0.4, 0.4, 0. , 0.2, 0.4, 0.2,
       0.4, 0.8, 0.4, 0. ])

In [85]:
som_df = pd.DataFrame(x2, columns=["X"])

som_df['Y']=y2
som_df['umatrix']= som_gp.distance_map(scaling='mean').reshape(m*n)
som_df['hits_flat'] = hits_labels
som_df['hits_pct'] = hits_pct*size*.75
som_df['coords'] = coords
som_df['radius'] = hits_flat*radius_multiplier
som_df['node_index'] = node_indices

for i in range(len(features_scaled)):
    som_df[features[i]] = som_gp.get_weights()[:,:,i].reshape(m*n)


som_df


X           Y   umatrix hits_flat   hits_pct   coords  radius  \
0      0.000000    0.000000  0.369853         5  33.333333   (0, 0)     1.5   
1    -22.222222   38.490018  0.387990         2  13.333333   (0, 1)     0.6   
2      0.000000   76.980036  0.256145         2  13.333333   (0, 2)     0.6   
3    -22.222222  115.470054  0.246051         4  26.666667   (0, 3)     1.2   
4      0.000000  153.960072  0.165134         2  13.333333   (0, 4)     0.6   
..          ...         ...       ...       ...        ...      ...     ...   
103  333.333333  269.430126  0.370037         1   6.666667   (8, 7)     0.3   
104  355.555556  307.920144  0.380534         2  13.333333   (8, 8)     0.6   
105  333.333333  346.410162  0.345622         4  26.666667   (8, 9)     1.2   
106  355.555556  384.900179  0.447622         2  13.333333  (8, 10)     0.6   
107  333.333333  423.390197  0.295806             0.000000  (8, 11)     0.0   

     node_index  TotPop90  PctRural   PctBach    PctEld     PctFB    PctPov  \
0             0 -0.455694  1.127259 -0.455378  1.723499 -0.536395  1.836006   
1             1 -0.405504  1.087627 -0.726293  0.396784 -0.686585  1.113347   
2             2 -0.406363  1.127259 -0.699416  0.879939 -0.541772  1.388610   
3             3 -0.435216  1.127259 -0.881401  0.263180 -0.763775  0.822376   
4             4 -0.309611  0.795587 -0.590883  0.347276 -0.699168  0.409056   
..          ...       ...       ...       ...       ...       ...       ...   
103         103  0.391942 -0.001071  0.181702 -0.732727  1.172372 -1.132139   
104         104  0.122333 -1.244629  0.317047 -1.955546  0.502800 -1.411787   
105         105  0.275708 -0.420296  1.291948 -1.407131  0.635073 -1.806814   
106         106 -0.006665  0.167292  2.896149 -1.271257  0.649294 -1.934866   
107         107  0.063098  0.356215  1.635126 -1.233682  0.299535 -1.847858   

     PctBlack  
0    1.828593  
1    2.532457  
2    0.916913  
3    1.155206  
4    0.961609  
..        ...  
103 -1.362380  
104 -0.787616  
105 -1.221403  
106 -1.235112  
107 -1.264567  

[108 rows x 15 columns]

In [21]:

# size = np.min([PLOT_WIDTH / m, PLOT_HEIGHT / n])


# c2 = hitsmatrix.reshape(m*n)
# x2 = xx.reshape(m*n) * size# / (np.sqrt(3)/2)
# y2 = yy.reshape(m*n) * size 
# # y2 = yy.reshape(m*n) #* np.sqrt(3) / 2 #* size
# # wy = yy[(i, j)] * np.sqrt(3) / 2


# hits_labels = [ i.astype(int).astype(str) if i > 0 else '' for i in c2 ]
# hits_labels_color = [ 1 if i.astype(int) > (.75*np.mean([max(c2), min(c2)])) else 0 for i in c2 ] 


# node_indices = list(range(m*n))
# coords = ["{}".format(np.unravel_index(i,weights.shape[:2])) for i in range(m*n) ]

# radius_multiplier = .3
# # hits_long = hitsmatrix.reshape((m*n))

# main_source = ColumnDataSource(dict(
#         x=x2,
#         y=y2,
#         c=c2,
#         umatrix_vals=umatrix_vals,
#         text=hits_labels,
#         label_colors = hits_labels_color,
#         umat_flat = umat_flat,
#         hits_flat = hits_flat,
#         hits_pct = hits_pct*size*.75,
#         coords=coords,
#         node_labels=coords,
#         radius=hits_flat*radius_multiplier,
#         index=node_indices,

#     )
# )

# plot = figure( width=PLOT_WIDTH,
#             height= PLOT_HEIGHT,
#             tools='tap,reset,save',
#             toolbar_location='above',
#             match_aspect=True,
#             aspect_scale=1,
#             title="SOM Grid Map",
#             outline_line_width=0,
#             name="hexwrapper"

#             )
# plot.toolbar.logo = None


# cmap = umatrix_cmap
# bg_hex = plot.scatter(source=main_source,
#                 size=size*1.05,
#                 marker="hex", 
#                 line_join='miter',
#                 fill_color={"field":"umat_flat", "transform":cmap},
#                 line_color={"field":"umat_flat", "transform":cmap},
#                 line_width=1,
#                 angle=90, 
#                 angle_units='deg',
#                 alpha=1,
#                 hover_fill_alpha=1,
#                 hover_line_width=4,
#                 hover_line_color=CONTRAST_COLOR1,
#                 nonselection_alpha=.25,
#                 selection_line_color=CONTRAST_COLOR1,
#                 selection_fill_alpha=1.0,
#                 selection_line_width=6,

# )

# um_colorbar = ColorBar(
#                         color_mapper=cmap, 
#                         location=(0,0),
#                         width=10,
#                         height=int(PLOT_HEIGHT/2),
#                         ticker=BasicTicker(min_interval=.1)
#                         )


# hits_hex = plot.scatter(source=main_source,
#             size='hits_pct',
#             marker="hex", 
#             line_join='miter',
#             fill_color="#fafafa",
#             line_width=0,
#             angle=90, 
#             angle_units='deg',
#             alpha=1,
#             nonselection_alpha=1,
#             selection_alpha=1,
       
# )

# tooltips = [
#     ("HITS", "@hits_flat"),
#     ("Average Dist", "@umat_flat")
# ]

# plot.add_tools(HoverTool(tooltips=tooltips, renderers=[bg_hex]))
# plot.grid.visible = False
# plot.axis.visible = False

# colorbar_plot = figure(width=60, #height=PLOT_HEIGHT,
#                         toolbar_location=None, 
#                         outline_line_width=0,
#                         name="colorbar_plot"
#                         )



# colorbar_plot.add_layout(um_colorbar, 'right')

# geo_cmap_col = 'PctRural'
# lx_cmap = LinearColorMapper(palette="Magma256", 
#                             low = 0, 
#                             high = max(c))


# lx_plot = figure(title = 'test', 
#            aspect_ratio=1, 
#             match_aspect=True,
#            height=PLOT_HEIGHT)

# # lx_plot.xgrid.grid_line_color = None
# # lx_plot.ygrid.grid_line_color = None

# # pt_shapes = lx_plot.patches('xs','ys', 
# #                 source = geosource,
# #                 fill_color = {"field":geo_cmap_col, "transform": lx_cmap},
# #                 # fill_color = "#DEDEDE",
# #                 line_color = 'black', 
# #                 line_width = 1, 
# #                 fill_alpha = 0.75)
# # lx_plot.axis.visible = False

# # lx_plot.add_tools(HoverTool(renderers=[pt_shapes]))




# show(row(plot, colorbar_plot, lx_plot))



# Calculate Statistics

In [22]:
stat_details = {
    "gwr" : {
        "summary": "",
        "x_suffix": "_",
        "y_suffix": "_",
        "x_suffix": "_",
        "combinations": []
    }
}

In [23]:
gp_df['_jitter'] = 1

In [24]:
feats['x'] = ['PctFB', 'PctBlack', 'PctRural']
feats['y'] = 'PctBach'

feats_yx = [feats['y']]+feats['x']

feats

{'all': ['TotPop90',
  'PctRural',
  'PctBach',
  'PctEld',
  'PctFB',
  'PctPov',
  'PctBlack'],
 'geo': {'x': 'X', 'y': 'Y'},
 'suf': {'scaled': '_std'},
 'x': ['PctFB', 'PctBlack', 'PctRural'],
 'y': 'PctBach'}

In [25]:

for f in feats_yx:
    gp_df['{}_jit'.format(f)] = f


### GWR / MGWR 

In [26]:
gp_df_gwr = gp_df.copy()

stats_params = {}

stats_params['bw'] = {'min': 2, 'multi': [2]}


def get_gwr_mgwr(df, geox, geoy, x_feats, y_feats, bw_params):

    g_y = df[y_feats].values.reshape((-1,1))
    g_X = df[x_feats].values
    u = df[geox]
    v = df[geoy]
    
    g_coords = list(zip(u,v))

    #Calibrate GWR model
    g_selector = Sel_BW(g_coords, g_y, g_X)
    g_bw = g_selector.search(bw_min=bw_params['min'])
    g_results = GWR(g_coords, g_y, g_X, g_bw).fit()

    
    #Calibrate MGWR model
    m_selector = Sel_BW(g_coords, g_y, g_X, multi=True)
    m_bw = m_selector.search(multi_bw_min=bw_params['multi'])
    m_results = MGWR(g_coords, g_y, g_X, m_selector).fit()

    
    return g_results, m_results


def get_gwr_params(feats, results, prefix='gwr', suffix='filter_t'):
    results_feats = [prefix+'_intercept'] + [ (prefix + '_' + f) for f in feats]

    res_df = pd.DataFrame(results.params, columns=results_feats)

    ## Mask non-significant t-vals
    filtered_results = results.filter_tvals()
    results_feats_filt = [prefix+'_intercept_'+suffix] + [ (prefix + '_' + f + '_' + suffix) for f in feats]
    res_df[results_feats_filt] = res_df[results_feats]
    
    for fi in range(len(results_feats_filt)):
        res_df.loc[filtered_results[:, fi]==0, results_feats_filt[fi]] = 0
    
    
    return res_df


## Get scaled features

scaled_x_feats = ["{}{}".format(i, feats['suf']['scaled']) for i in feats['x']]
scaled_y_feat = "{}{}".format(feats['y'], feats['suf']['scaled'])


gwr_results, mgwr_results = get_gwr_mgwr(gp_df,
                                         feats['geo']['x'], feats['geo']['y'],
                                         scaled_x_feats, scaled_y_feat,
                                         stats_params['bw'])


## Get GWR Coefficients
## Get MGWR Coefficients

gwr_mgwr_df = pd.concat([
    get_gwr_params(feats['x'], gwr_results),
    get_gwr_params(feats['x'], mgwr_results, prefix='mgwr')], 
                        axis=1)

## Get stat summaries

details['gwr_summary'] = gwr_results.summary(as_str=True)
details['mgwr_summary'] = mgwr_results.summary(as_str=True)


gm_cols = [i for i in gwr_mgwr_df.columns if i not in gp_df.columns]

gp_df = pd.concat([gp_df, gwr_mgwr_df[gm_cols]], axis=1)

Backfitting:   0%|          | 0/200 [00:00<?, ?it/s]

Inference:   0%|          | 0/1 [00:00<?, ?it/s]

In [90]:
gwr_mgwr_df.columns

Index(['gwr_intercept', 'gwr_PctFB', 'gwr_PctBlack', 'gwr_PctRural',
       'gwr_intercept_filter_t', 'gwr_PctFB_filter_t', 'gwr_PctBlack_filter_t',
       'gwr_PctRural_filter_t', 'mgwr_intercept', 'mgwr_PctFB',
       'mgwr_PctBlack', 'mgwr_PctRural', 'mgwr_intercept_filter_t',
       'mgwr_PctFB_filter_t', 'mgwr_PctBlack_filter_t',
       'mgwr_PctRural_filter_t'],
      dtype='object')

In [89]:
gwr_mgwr_df.columns

Index(['gwr_intercept', 'gwr_PctFB', 'gwr_PctBlack', 'gwr_PctRural',
       'gwr_intercept_filter_t', 'gwr_PctFB_filter_t', 'gwr_PctBlack_filter_t',
       'gwr_PctRural_filter_t', 'mgwr_intercept', 'mgwr_PctFB',
       'mgwr_PctBlack', 'mgwr_PctRural', 'mgwr_intercept_filter_t',
       'mgwr_PctFB_filter_t', 'mgwr_PctBlack_filter_t',
       'mgwr_PctRural_filter_t'],
      dtype='object')

In [27]:
gwr_mgwr_df[['gwr_PctFB','mgwr_PctFB']]

gwr_PctFB  mgwr_PctFB
0     0.726991    0.342926
1     0.729866    0.285309
2     0.730012    0.316351
3     0.729748    0.468492
4     0.729682    0.736058
..         ...         ...
167   0.128551   -0.089908
168   0.123242   -0.092556
169   0.127391    0.083569
170   0.126401    0.245129
171   0.123542    0.031393

[172 rows x 2 columns]

In [28]:
from bokeh.io import show
from bokeh.models import CustomJS, RadioButtonGroup


# show(column(radio_button_group,radio_button_group2,radio_button_group3))

In [29]:
mgwr_results.summary(as_str=True)

'===========================================================================\nModel type                                                         Gaussian\nNumber of observations:                                                 172\nNumber of covariates:                                                     4\n\nGlobal Regression Results\n---------------------------------------------------------------------------\nResidual sum of squares:                                             76.800\nLog-likelihood:                                                    -174.716\nAIC:                                                                357.432\nAICc:                                                               359.794\nBIC:                                                               -787.979\nR2:                                                                   0.553\nAdj. R2:                                                              0.546\n\nVariable                              Est.  

## Global Spatial Autocorrelation: Moran's I

In [30]:
gp_df_moran = gp_df.copy()

WEIGHTS_MX = {
    'Queen': pysal_weights.Queen, 
    'Rook': pysal_weights.Rook, 
    'KNN': pysal_weights.KNN, 
    'lat2W': pysal_weights.lat2W
}



def get_w(df, 
          weights_mx_name = 'KNN',
          weights_params = dict(k=8),          
         ):
    try:
        return WEIGHTS_MX[weights_mx_name].from_dataframe(df, **weights_params)
    except:
        return pysal_weights.KNN.from_dataframe(df, **weights_params)
        



def get_lags(w, df, feats):
    
    lags_df = pd.DataFrame()
    
    for f in feats:
        lags_df[f+'_std'] = df[f+'_std']
        lags_df[f+'_lag'] = pysal_weights.lag_spatial(w, df[f+'_std'])
        lags_df[f+'_lag_std'] = lags_df[f+'_lag'] - lags_df[f+'_lag'].mean()
        
    
    return lags_df

w = get_w(gp_df )

# Row-standardization
w.transform = "R"

## Get spatial lags
lags_df = get_lags(w, gp_df, [feats['y']]+feats['x'])
lags_reg = linregress(gp_df["PctBlack_std"], lags_df["PctBlack_lag_std"])

scaled_lags = pd.concat([gp_df_orig[features_scaled],lags_df], axis=1)
scaled_lags[['PctBlack_std', 'PctBlack_lag_std',]]

lags_reg = linregress(lags_df["PctBlack_std"], lags_df["PctBlack_lag_std"])
keep_cols_lags = [c for c in lags_df.columns if c not in gp_df_moran.columns]

gp_df = pd.concat([gp_df_moran, lags_df[keep_cols_lags]], axis=1).drop_duplicates()
# gp_df.shape
# orig_cds = ColumnDataSource(pd.concat([gp_df_orig[features_scaled],lags_df], axis=1))

In [31]:
# gp_df.columns.to_list()

# gp_df.to_csv("./stats.csv", index=False)

## Local Spatial Autocorellation: LISA

In [32]:
gp_df_lisa = gp_df.copy()

spots_mapper = {
    0: "NS",
    1: "HH",
    2: "LH",
    3: "LL",
    4: "HL",
}


hilo_cmap = {
    "LH" : "#a6cee3",
    "LL" : "#1f78b4",
    "HH" : "#d93b43",
    "HL" : "#e08d49",
    "NS" : "#eaeaea",
}


    
def get_lisa(w, df, feats, p=0.05):
    
    lisa_df = pd.DataFrame()
    lisa_models = {}
    
    for f in feats:
        lisa_f   = f + "_lisa"
        lisa_fc  = lisa_f + "_clust"
        lisa_fcf = lisa_fc + "_filt"
        
        lisa = esda.moran.Moran_Local(df[f], w)
        lisa_df[lisa_f] = lisa.Is
        lisa_df[lisa_fc] = lisa.q

        lisa_models[f] = lisa

        sig = lisa.p_sim >= p
        lisa_df[lisa_fcf] = lisa.q
        lisa_df.loc[sig, lisa_fcf] = 0
        lisa_df[lisa_fcf] = lisa_df[lisa_fcf].map(spots_mapper)

        # Take the standardized values
        lisa_df[f+'_std'] = df[f+'_std']

        # Take the lag of std
        lisa_df[f+'_lag'] = pysal_weights.lag_spatial(w, lisa_df[f+'_std'])

        # Standardize the lag
        lisa_df[f+'_lag_std'] = lisa_df[f+'_lag'] - lags_df[f+'_lag'].mean()
    
    return lisa_df, lisa_models

lisa_df, lisa_models = get_lisa(w, gp_df_lisa, [feats['y']]+feats['x'])

# lisa_cds = ColumnDataSource(lisa_df)

keep_cols_lisa = [c for c in lisa_df.columns if c not in gp_df_lisa.columns]

gp_df = pd.concat([gp_df_lisa, lisa_df[keep_cols_lisa]], axis=1).drop_duplicates()


## Moran Bivariate



https://pysal.org/notebooks/viz/splot/esda_morans_viz.html#Local-Bivariate-Moran-Statistics

In [33]:
gp_df_mbv = gp_df.copy()

def get_moran_bv(df, feats, w, spots_mapper=spots_mapper, p=0.05):

    f_combis = list(permutations(feats,2))
    
    mbv_df = pd.DataFrame()
    
    mbv_models = {}
    
    for fi in f_combis:
        mbv_name = "MBV_" + "_".join(fi)
        
        mbv = Moran_Local_BV(
            df["{}_std".format(fi[0])],
            df["{}_std".format(fi[1])],
            w)
        mbv_models[mbv_name] = mbv
        
        mbv_df[mbv_name] = mbv.q
        sig = mbv.p_sim >= p
        mbv_df.loc[sig, mbv_name] = 0
        mbv_df[mbv_name] = mbv_df[mbv_name].map(spots_mapper)

    
    return mbv_df, mbv_models

mbv_df, mbv_models = get_moran_bv(gp_df, [feats['y']]+feats['x'], w)

# colors5 = [hilo_cmap[i] for i in hilo_cmap]
# colors5

gp_df = pd.concat([gp_df_mbv, mbv_df], axis=1)

In [34]:
hilo_keys = list(hilo_cmap.keys())
hilo_keys

['LH', 'LL', 'HH', 'HL', 'NS']

In [55]:
mbv_df

MBV_PctBach_PctFB MBV_PctBach_PctBlack MBV_PctBach_PctRural  \
0                  NS                   HL                   HH   
1                  NS                   HL                   HH   
2                  NS                   LL                   LH   
3                  NS                   LL                   LH   
4                  NS                   LL                   NS   
..                ...                  ...                  ...   
167                NS                   HH                   NS   
168                LL                   LH                   NS   
169                NS                   NS                   NS   
170                NS                   NS                   NS   
171                NS                   NS                   NS   

    MBV_PctFB_PctBach MBV_PctFB_PctBlack MBV_PctFB_PctRural  \
0                  NS                 LL                 LH   
1                  NS                 HL                 HH   
2                  NS                 LL                 LH   
3                  NS                 LL                 LH   
4                  NS                 LL                 NS   
..                ...                ...                ...   
167                NS                 HH                 NS   
168                NS                 HH                 NS   
169                HL                 NS                 NS   
170                NS                 NS                 NS   
171                NS                 NS                 NS   

    MBV_PctBlack_PctBach MBV_PctBlack_PctFB MBV_PctBlack_PctRural  \
0                     NS                 NS                    LH   
1                     NS                 NS                    LH   
2                     NS                 NS                    LH   
3                     NS                 NS                    LH   
4                     NS                 NS                    NS   
..                   ...                ...                   ...   
167                   NS                 NS                    NS   
168                   NS                 HL                    NS   
169                   HL                 NS                    NS   
170                   NS                 NS                    NS   
171                   NS                 NS                    NS   

    MBV_PctRural_PctBach MBV_PctRural_PctFB MBV_PctRural_PctBlack  
0                     NS                 NS                    HL  
1                     NS                 NS                    HL  
2                     NS                 NS                    HL  
3                     NS                 NS                    HL  
4                     NS                 NS                    HL  
..                   ...                ...                   ...  
167                   NS                 NS                    LH  
168                   NS                 LL                    LH  
169                   LL                 NS                    NS  
170                   NS                 NS                    NS  
171                   NS                 NS                    NS  

[172 rows x 12 columns]

# Get GEOJSON

In [35]:
geo_df_columns

Index(['AREA', 'PERIMETER', 'G_UTM_', 'G_UTM_ID', 'AREANAME', 'Latitude',
       'Longitud', 'TotPop90', 'PctRural', 'PctBach', 'PctEld', 'PctFB',
       'PctPov', 'PctBlack', 'X', 'Y', 'AreaKey', 'geometry'],
      dtype='object')

In [36]:
geo_data_cols = [i for i in gp_df if i not  in geo_df_columns]


In [37]:
gp_df[geo_data_cols]


_DF_ID  TotPop90_std  PctRural_std  PctBach_std  PctEld_std  PctFB_std  \
0         0     -0.357026      1.127259     0.109774    1.775865  -0.003515   
1         1     -0.417300      1.127259     0.073810    3.658938   0.186946   
2         2     -0.352778      1.127259    -0.159956    1.896407  -0.210537   
3         3     -0.303527      1.127259    -0.573542    1.814960  -0.458963   
4         4     -0.178461      0.713538    -0.987128   -1.315893  -0.525211   
..      ...           ...           ...          ...         ...        ...   
167     167     -0.186293     -0.452404     0.127756    0.420574   0.336002   
168     168     -0.389515     -0.023638    -0.573542    0.805007   3.772570   
169     169      0.435281     -0.843558     0.954927   -0.892365   0.327721   
170     170     -0.471735      1.127259    -1.130984   -0.638248   0.410530   
171     171     -0.310842     -0.166560    -0.339776    0.635596   0.518181   

     PctPov_std  PctBlack_std  BMU  _jitter  ... MBV_PctBach_PctRural  \
0     -0.789646     -1.578375   11        1  ...                   HH   
1     -0.734847     -1.598751   11        1  ...                   HH   
2     -0.145759     -1.592929   11        1  ...                   LH   
3     -0.296456     -1.597005   11        1  ...                   LH   
4     -1.104739     -1.583614   71        1  ...                   NS   
..          ...           ...  ...      ...  ...                  ...   
167    0.539228      0.699172   50        1  ...                   NS   
168    1.333811      0.307355  101        1  ...                   NS   
169    0.073437      0.257286   74        1  ...                   NS   
170   -0.652648     -0.930392   47        1  ...                   NS   
171    0.895420      0.815611   38        1  ...                   NS   

    MBV_PctFB_PctBach MBV_PctFB_PctBlack MBV_PctFB_PctRural  \
0                  NS                 LL                 LH   
1                  NS                 HL                 HH   
2                  NS                 LL                 LH   
3                  NS                 LL                 LH   
4                  NS                 LL                 NS   
..                ...                ...                ...   
167                NS                 HH                 NS   
168                NS                 HH                 NS   
169                HL                 NS                 NS   
170                NS                 NS                 NS   
171                NS                 NS                 NS   

     MBV_PctBlack_PctBach  MBV_PctBlack_PctFB  MBV_PctBlack_PctRural  \
0                      NS                  NS                     LH   
1                      NS                  NS                     LH   
2                      NS                  NS                     LH   
3                      NS                  NS                     LH   
4                      NS                  NS                     NS   
..                    ...                 ...                    ...   
167                    NS                  NS                     NS   
168                    NS                  HL                     NS   
169                    HL                  NS                     NS   
170                    NS                  NS                     NS   
171                    NS                  NS                     NS   

     MBV_PctRural_PctBach  MBV_PctRural_PctFB  MBV_PctRural_PctBlack  
0                      NS                  NS                     HL  
1                      NS                  NS                     HL  
2                      NS                  NS                     HL  
3                      NS                  NS                     HL  
4                      NS                  NS                     HL  
..                    ...                 ...                    ...  
167                    NS                  NS               

In [38]:
# geosource = GeoJSONDataSource(geojson = gp_df[geo_df_columns].to_json())
geosource = GeoJSONDataSource(geojson = gp_df.to_json())
geodata_cds = ColumnDataSource(gp_df[geo_data_cols])

# Visualize Bokeh

In [39]:
mpl_colors.Colormap('seismic', N=256)
seismic = [mpl.colormaps['seismic'].resampled(256)(i) for i in range(256) ]
seismic = [mpl_colors.to_hex(i) for i in seismic]

In [40]:
PLOT_WIDTH = 400
PLOT_HEIGHT = 700
CONTRAST_COLOR1 = "#ff6361"
CONTRAST_COLOR2 = "#bc5090"
m=som_params['m']
n=som_params['n']

xx, yy = som_gp.get_euclidean_coordinates()

weights = som_gp.get_weights()

umatrix = som_gp.distance_map(scaling='mean')
umatrix_vals = umatrix.reshape(m*n)
c = umatrix.reshape(m*n)


hitsmatrix = som_gp.activation_response(gp_df[features_scaled].values)
    

hits_flat = hitsmatrix.reshape(m*n)
umat_flat = umatrix.reshape(m*n)

hits_pct = hitsmatrix.reshape(m*n) / hitsmatrix.max()

# hits_labels = [ i.astype(int).astype(str) if i > 0 else '' for i in c2 ]
# hits_labels_color = [ 1 if i.astype(int) > (.75*np.mean([max(c2), min(c2)])) else 0 for i in c2 ] 

palette = 'Viridis256'

umatrix_cmap = LinearColorMapper(palette=palette,
                            low = 0, 
                            high = max(c))

size = np.min([PLOT_WIDTH / m, PLOT_HEIGHT / n])


c2 = hitsmatrix.reshape(m*n)
x2 = xx.reshape(m*n) * size
y2 = yy.reshape(m*n) * size 


hits_labels = [ i.astype(int).astype(str) if i > 0 else '' for i in c2 ]
hits_labels_color = [ 1 if i.astype(int) > (.75*np.mean([max(c2), min(c2)])) else 0 for i in c2 ] 


node_indices = list(range(m*n))
coords = ["{}".format(np.unravel_index(i,weights.shape[:2])) for i in range(m*n) ]

radius_multiplier = .3

main_source = ColumnDataSource(dict(
        x=x2,
        y=y2,
        c=c2,
        umatrix_vals=umatrix_vals,
        text=hits_labels,
        label_colors = hits_labels_color,
        umat_flat = umat_flat,
        hits_flat = hits_flat,
        hits_pct = hits_pct*size*.75,
        coords=coords,
        node_labels=coords,
        radius=hits_flat*radius_multiplier,
        index=node_indices,


    )
)

plot = figure( width=PLOT_WIDTH,
            height= PLOT_HEIGHT,
            tools='tap,reset,save',
            toolbar_location='above',
            match_aspect=True,
            aspect_scale=1,
            title="SOM Grid Map",
            outline_line_width=0,
            name="hexwrapper"

            )
plot.toolbar.logo = None


bg_all = AllIndices()
bg_view = CDSView(filter=bg_all)

cmap = umatrix_cmap
bg_hex = plot.scatter(source=main_source,
                size=size*1.05,
                marker="hex", 
                line_join='miter',
                fill_color={"field":"umat_flat", "transform":cmap},
                line_color={"field":"umat_flat", "transform":cmap},
                line_width=1,
                angle=90, 
                angle_units='deg',
                alpha=1,
                hover_fill_alpha=1,
                hover_line_width=4,
                hover_line_color=CONTRAST_COLOR1,
                nonselection_alpha=.25,
                selection_line_color=CONTRAST_COLOR1,
                selection_fill_alpha=1.0,
                selection_line_width=6,
                view = bg_view,

)

um_colorbar = ColorBar(
                        color_mapper=cmap, 
                        location=(0,0),
                        width=10,
                        height=int(PLOT_HEIGHT/2),
                        ticker=BasicTicker(min_interval=.1)
                        )


hits_hex = plot.scatter(source=main_source,
            size='hits_pct',
            marker="hex", 
            line_join='miter',
            fill_color="#fafafa",
            line_width=0,
            angle=90, 
            angle_units='deg',
            alpha=1,
            nonselection_alpha=1,
            selection_alpha=1,
       
)

tooltips = [
    ("HITS", "@hits_flat"),
    ("Average Dist", "@umat_flat")
]

plot.add_tools(HoverTool(tooltips=tooltips, renderers=[bg_hex]))
plot.grid.visible = False
plot.axis.visible = False

colorbar_plot = figure(width=60, #height=PLOT_HEIGHT,
                        toolbar_location=None, 
                        outline_line_width=0,
                        name="colorbar_plot"
                        )



colorbar_plot.add_layout(um_colorbar, 'right')

# continues below

In [41]:
# continued from above


# geo_cmap_col = 'gwr_rural_sig'
# geo_cmap_col = 'PctRural'
geo_cmap_col = 'mgwr_intercept_filter_t'

geo_palette = interp_palette(seismic, 256)

lx_cmap = LinearColorMapper(palette=geo_palette, 
                            low = np.min([0,gp_df[geo_cmap_col].min()]),
                            high = np.max([0,gp_df[geo_cmap_col].max()])
                           )


lx_plot = figure(title = 'test', 
                 aspect_ratio=1, 
                 match_aspect=True,
                 height=PLOT_HEIGHT,
                 tools='tap,reset,save',
                 
                )

lx_plot.xgrid.grid_line_color = None
lx_plot.ygrid.grid_line_color = None

geo_all = AllIndices()
geo_view = CDSView(filter=geo_all)

pt_shapes = lx_plot.patches('xs','ys', 
                            source = geosource,
                            fill_color = {"field":geo_cmap_col, "transform": lx_cmap},
                
                            line_color = 'black', 
                            selection_line_color = 'orange', 
                
                            line_width = 1, 
                            selection_line_width = 4, 
                            fill_alpha = 0.75,
                            nonselection_fill_alpha = 0.5,

                            view = geo_view,
                            
                            name = 'geo_units'
                           )

lx_plot.axis.visible = False

lx_plot.add_tools(HoverTool(renderers=[pt_shapes]))


geo_color_bar = pt_shapes.construct_color_bar(
    major_tick_line_color=None,
)

lx_plot.add_layout(geo_color_bar, "right")


# continues below

In [42]:
hex_cb = """


var bmus = cb_obj.indices

if (cb_obj.indices.length == 0) {

    var indices = []
    
    for (var i=0; i<geo_source.get_length(); i++) {
        indices.push(i)
    }
    
    geo_source.selected.indices = []

    geo_index.indices = indices
    geo_view.filter = geo_index
    
    geo_source.change.emit()
    
    
} else {

    var selected = []
    var indices = []
    

    for (var i=0; i<geo_source.get_length(); i++) {
        indices.push(i)
        
        var geo_unit = geo_source.data
        if (bmus.includes(geo_unit.BMU[i])) {
            selected.push(i)
        }
    }

    
    geo_index.indices = indices
    geo_view.filter = geo_index

    geo_source.selected.indices = selected
    geo_source.change.emit()
    
}


"""


main_source.selected.js_on_change('indices', 
                                CustomJS(args=dict(
                                            geo_source  = geosource,
                                            main_source = main_source,
                                            geo_plot    = lx_plot,
                                            geo_view    = geo_view,
                                            geo_all     = AllIndices(),
                                            geo_index   = IndexFilter(indices=[]),
                                            ),
                                        code=hex_cb
                                        ))





In [43]:
geo_cb = """"""

geo_cb_x = """

var geo_units = cb_obj.indices

//var bmus = cb_obj.indices

console.log(geo_units)
console.log(geo_source)

if (cb_obj.indices.length == 0) {

    var indices = []
    
    for (var i=0; i<geo_source.get_length(); i++) {
        indices.push(i)
    }
    
    //geo_source.selected.indices = []

    //geo_index.indices = indices
    //geo_view.filter = geo_index
    
    //geo_source.change.emit()
    
    
} else {

    var selected = []
    var indices = []
    

    for (var i=0; i<geo_source.get_length(); i++) {
        indices.push(i)
        
        var geo_unit = geo_source.data
        //if (bmus.includes(geo_unit.BMU[i])) {
        //    selected.push(i)
        //}
    }

    
    //geo_index.indices = indices
    //geo_view.filter = geo_index

    //geo_source.selected.indices = selected
    //geo_source.change.emit()
    
}


"""


geosource.selected.js_on_change('indices', 
                                CustomJS(args=dict(
                                            geo_source   = geosource,
                                            main_source  = main_source,
                                            geo_plot     = lx_plot,
                                            hex_view     = bg_view,
                                            hex_all      = AllIndices(),
                                            hex_index    = IndexFilter(indices=[]),
                                            ),
                                        code=geo_cb
                                        ))



# show(row(plot, colorbar_plot, lx_plot))


In [44]:
# scatter_feat = "PctBlack"
# scatter_feat_x = "{}_std".format(scatter_feat)
# scatter_feat_y = "{}_lag_std".format(scatter_feat)

# scatter_plot = figure(title="Spatial Autocorrelation: {}".format(scatter_feat), 
#                       x_axis_label=scatter_feat_x, 
#                       y_axis_label=scatter_feat_y, 
#                       aspect_ratio=1, 
#                      match_aspect=True,
#                      height=PLOT_HEIGHT,
#                      tools='tap,reset,save,box_select',
#                      )

# lags_reg = linregress(lags_df[scatter_feat_x], lags_df[scatter_feat_y])



# scatter_plot.hspan(y=[0], line_color='black')
# scatter_plot.vspan(x=[0], line_color='black')

# slope = Slope(gradient=lags_reg.slope, 
#               y_intercept=lags_reg.intercept,
#               line_color='red', 
#               line_dash='dashed', 
#               line_width=4)


# # add scatter data with legend
# scatter_dots = scatter_plot.circle(
#     x=scatter_feat_x, 
#     y=scatter_feat_y, 
#     source=geosource,
#     radius=0.05, 
#     selection_fill_color = "orange",
#     selection_line_color = "orange",
    
#     fill_alpha = 0.75,
#     nonselection_fill_alpha = 0.5,
#     selection_fill_alpha = 1,
    
#     )

# scatter_plot.add_layout(slope)

# scatter_plot.add_tools(HoverTool(renderers=[scatter_dots]))

# # show(scatter_plot)

In [45]:
# show(row(plot, colorbar_plot, lx_plot, scatter_plot))


In [46]:
# continued from above

scatter_feat = "PctBlack"

# geo_cmap_col = 'gwr_rural_sig'
# geo_cmap_col = 'PctRural'
# geo_cmap_col = 'mgwr_intercept_filter_t'
geo_cmap_col = scatter_feat #+ "_lisa"
scatter_feat_lisa = scatter_feat + "_lisa"

geo_palette = interp_palette(seismic, 256)

lx_cmap = LinearColorMapper(palette=geo_palette, 
                            low = np.min([0,gp_df[geo_cmap_col].min()]),
                            high = np.max([0,gp_df[geo_cmap_col].max()])
                           )


lx_plot = figure(title = geo_cmap_col, 
                 aspect_ratio=1, 
                 match_aspect=True,
                 height=PLOT_HEIGHT,
                 tools='tap,reset,save',
                 
                )

lx_plot.xgrid.grid_line_color = None
lx_plot.ygrid.grid_line_color = None

geo_all = AllIndices()
geo_view = CDSView(filter=geo_all)

pt_shapes = lx_plot.patches('xs','ys', 
                            source = geosource,
                            fill_color = {"field":geo_cmap_col, "transform": lx_cmap},
                            color = {"field":geo_cmap_col, "transform": lx_cmap},
    
                            line_color = 'black', 
                
                            line_width = 1, 
                            selection_line_width = 4, 
                            fill_alpha = 0.75,
                            nonselection_fill_alpha = 0.25,

                            view = geo_view,
                            name='geo_units'
                           )

lx_plot.axis.visible = False

lx_plot.add_tools(HoverTool(renderers=[pt_shapes]))


geo_color_bar = pt_shapes.construct_color_bar(
    major_tick_line_color=None,
)

lx_plot.add_layout(geo_color_bar, "right")


# continues below

In [47]:
div = Div(text="""
Your HTML-supported text is initialized with the <b>text</b> argument.  The
remaining div arguments are <b>width</b> and <b>height</b>. For this example, those values
are <i>200</i> and <i>100</i>, respectively.""",
width=PLOT_WIDTH, height=int(PLOT_HEIGHT*.3))

In [48]:
scatter_feat = "PctBlack"
scatter_feat_x = "{}_std".format(scatter_feat)
scatter_feat_y = "{}_lag_std".format(scatter_feat)
scatter_feat_hl = "{}_lisa_clust_filt".format(scatter_feat)

hilo_cmap = {
    "NS" : "#dedede",
    "LL" : "#1f78b4",
    "LH" : "#7696A7",
    "HL" : "#e08d49",
    "HH" : "#d93b43",
}

scatter_plot = figure(title="Spatial Autocorrelation: {}".format(scatter_feat), 
                      x_axis_label=scatter_feat_x, 
                      y_axis_label=scatter_feat_y, 
                      aspect_ratio=1, 
                     match_aspect=True,
                     height=int(PLOT_HEIGHT*.7),
                     tools='tap,reset,save,box_select',
                      
                     )

lags_reg = linregress(lags_df[scatter_feat_x], lags_df[scatter_feat_y])



scatter_plot.hspan(y=[0], line_color='black')
scatter_plot.vspan(x=[0], line_color='black')

slope = Slope(gradient=lags_reg.slope, 
              y_intercept=lags_reg.intercept,
              line_color='red', 
              line_dash='dashed', 
              line_width=4)


# add scatter data with legend
scatter_dots = scatter_plot.circle(
    x=scatter_feat_x, 
    y=scatter_feat_y, 
    source=geosource,
    radius=0.05, 

    # selection_fill_color = "orange",
    selection_line_color = "#5e4c54",
    selection_line_width = 1,
    line_width = 1,
    
    fill_alpha = 0.75,
    nonselection_fill_alpha = 0.25,
    selection_fill_alpha = 1,
    name="scatter_dots",
    # legend_field = scatter_feat_hl,
    color = factor_cmap(scatter_feat_hl, 
                       palette=list(hilo_cmap.values()), 
                       factors=list(hilo_cmap.keys()))
    
    )

scatter_plot.add_layout(slope)

scatter_plot.add_tools(HoverTool(renderers=[scatter_dots]))


color_bar = scatter_dots.construct_color_bar(
    # location=(1, -2),
    major_tick_line_color=None,
)

scatter_plot.add_layout(color_bar, "right")

# show(scatter_plot)

In [49]:

LABELS = ["GWR", "MGWR", "Global Moran", "Local Moran", "Bivariate Local Moran", "Features"]

radio_button_group = RadioButtonGroup(labels=LABELS, active=0)
radio_button_group.js_on_event("button_click", 
                               CustomJS(args=dict(btn=radio_button_group), code="""
    console.log('radio_button_group: active=' + btn.active, this.toString())
"""))


FEAT_OPTS = ["PctBach", "PctFB", "PctBlack"]

radio_button_group2 = RadioButtonGroup(labels=FEAT_OPTS, active=0)
radio_button_group2.js_on_event("button_click", CustomJS(args=dict(btn=radio_button_group2), code="""
    console.log('radio_button_group: active=' + btn.active, this.toString())
"""))
radio_button_group3 = RadioButtonGroup(labels=FEAT_OPTS, active=0)
radio_button_group3.js_on_event("button_click", CustomJS(args=dict(btn=radio_button_group3), code="""
    console.log('radio_button_group: active=' + btn.active, this.toString())
"""))



LABELS = ["Option 1", "Option 2", "Option 3"]

checkbox_button_group = CheckboxButtonGroup(labels=LABELS, active=[0, 1])
checkbox_button_group.js_on_event("button_click", CustomJS(args=dict(btn=checkbox_button_group), code="""
    console.log('checkbox_button_group: active=' + btn.active, this.toString())
"""))

lo1 = ["Option 11", "Option 12", "Option 13"]
lo2 = ["Option 21", "Option 22", "Option 23"]


In [53]:
show(row(plot, colorbar_plot, lx_plot, 
         column(column(radio_button_group,radio_button_group2,radio_button_group3), 
                scatter_plot)))


### Univariate Statistics Visualization

In [46]:
gp_df[features]


TotPop90  PctRural  PctBach  PctEld  PctFB  PctPov  PctBlack
0       11648     100.0     11.6   17.18   1.13    13.6      0.35
1        6754     100.0     11.4   22.96   1.36    14.0      0.00
2       11993     100.0     10.1   17.55   0.88    18.3      0.10
3       15992     100.0      7.8   17.30   0.58    17.2      0.03
4       26147      89.0      5.5    7.69   0.50    11.3      0.26
..        ...       ...      ...     ...    ...     ...       ...
167     25511      58.0     11.7   13.02   1.54    23.3     39.47
168      9010      69.4      7.8   14.20   5.69    29.1     32.74
169     75981      47.6     16.3    8.99   1.53    19.9     31.88
170      2334     100.0      4.7    9.77   1.63    14.6     11.48
171     15398      65.6      9.1   13.68   1.76    25.9     41.47

[172 rows x 7 columns]

In [47]:
feats_yx_std = ["{}_std".format(i) for i in feats_yx]

gp_df_wide = gp_df[feats_yx+feats_yx_std].copy()
gp_df_wide.reset_index(inplace=True)
gp_df_wide

index  PctBach  PctFB  PctBlack  PctRural  PctBach_std  PctFB_std  \
0        0     11.6   1.13      0.35     100.0     0.109774  -0.003515   
1        1     11.4   1.36      0.00     100.0     0.073810   0.186946   
2        2     10.1   0.88      0.10     100.0    -0.159956  -0.210537   
3        3      7.8   0.58      0.03     100.0    -0.573542  -0.458963   
4        4      5.5   0.50      0.26      89.0    -0.987128  -0.525211   
..     ...      ...    ...       ...       ...          ...        ...   
167    167     11.7   1.54     39.47      58.0     0.127756   0.336002   
168    168      7.8   5.69     32.74      69.4    -0.573542   3.772570   
169    169     16.3   1.53     31.88      47.6     0.954927   0.327721   
170    170      4.7   1.63     11.48     100.0    -1.130984   0.410530   
171    171      9.1   1.76     41.47      65.6    -0.339776   0.518181   

     PctBlack_std  PctRural_std  
0       -1.578375      1.127259  
1       -1.598751      1.127259  
2       -1.592929      1.127259  
3       -1.597005      1.127259  
4       -1.583614      0.713538  
..            ...           ...  
167      0.699172     -0.452404  
168      0.307355     -0.023638  
169      0.257286     -0.843558  
170     -0.930392      1.127259  
171      0.815611     -0.166560  

[172 rows x 9 columns]

In [48]:
gp_df_long = pd.concat([pd.melt(gp_df_wide, id_vars=['index'], value_vars=feats_yx),
                        pd.melt(gp_df_wide, id_vars=['index'], value_vars=feats_yx_std,
                               var_name='variable_std', value_name='value_std')],
                      axis=1)
gp_df_long.iloc[:,1:]

variable  value  index  variable_std  value_std
0     PctBach   11.6      0   PctBach_std   0.109774
1     PctBach   11.4      1   PctBach_std   0.073810
2     PctBach   10.1      2   PctBach_std  -0.159956
3     PctBach    7.8      3   PctBach_std  -0.573542
4     PctBach    5.5      4   PctBach_std  -0.987128
..        ...    ...    ...           ...        ...
683  PctRural   58.0    167  PctRural_std  -0.452404
684  PctRural   69.4    168  PctRural_std  -0.023638
685  PctRural   47.6    169  PctRural_std  -0.843558
686  PctRural  100.0    170  PctRural_std   1.127259
687  PctRural   65.6    171  PctRural_std  -0.166560

[688 rows x 5 columns]

In [49]:

for f in feats_yx:
    gp_df_wide['{}_jit'.format(f)] = f


In [50]:
gp_df_wide[feats_yx].quantile(.75)

PctBach      12.200
PctFB         1.385
PctBlack     40.660
PctRural    100.000
Name: 0.75, dtype: float64

In [51]:
boxplot_figs = []
feats_cds = ColumnDataSource(gp_df_wide)
iqr_df = gp_df_wide[feats_yx].describe().T.rename(columns={"25%":"q1",
                                                  "50%":"q2",
                                                  "75%":"q3"
                                                 })

iqr_df['iqr'] = (iqr_df['q3'] - iqr_df['q1'])*1.5
iqr_df['upper'] = iqr_df['q3'] + iqr_df['iqr']
iqr_df['lower'] = iqr_df['q1'] - iqr_df['iqr']
iqr_df['upper'] = iqr_df.apply(lambda row: np.min([row['max'],row['upper']]), axis=1)
iqr_df['lower'] = iqr_df.apply(lambda row: np.max([row['min'],row['lower']]), axis=1)

iqr_df


# iqr_df = pd.DataFrame(gp_df_wide[feats_yx].quantile(.75) - gp_df_wide[feats_yx].quantile(.25),
#                       columns=['iqr'])
# iqr_df["q3"] = gp_df_wide[feats_yx].quantile(.75)
# iqr_df["q2"] = gp_df_wide[feats_yx].quantile(.5)
# iqr_df["q1"] = gp_df_wide[feats_yx].quantile(.25)
# iqr_df["max"] = gp_df_wide[feats_yx].max()
# iqr_df["min"] = gp_df_wide[feats_yx].min()

# iqr_df["upper"] = gp_df_wide[feats_yx].quantile(.75) + 1.5*iqr_df['iqr']

# iqr_df["lower"] = gp_df_wide[feats_yx].quantile(.25) - 1.5*iqr_df['iqr']
iqr_df.reset_index(inplace=True)

iqr_cds = ColumnDataSource(iqr_df)

for f in feats_yx:

    univar_fig = figure(height=400, 
                        width=100,
                        x_range=[f], 
                        title=f,
                        toolbar_location=None,
                         tools='tap,reset,box_select',
                        
                       )
    univar_fig.xgrid.grid_line_color = None
    univar_fig.ygrid.grid_line_color = None

    


    
    feats_view = CDSView(filter=GroupFilter(column_name="variable", group=f))

    univar_fig.x_range = FactorRange(factors=[f])


    error = Whisker(base='index', 
                    upper="upper", 
                    lower="lower", 
                    source=iqr_cds,
                    line_width=2,
                    level="annotation"
                   )
    error.upper_head.size=20
    error.lower_head.size=20
    univar_fig.add_layout(error)

    cmap = factor_cmap("index", "TolRainbow7", iqr_df['index'].to_list())
    univar_fig.vbar("index", 0.5, "q2", "q3", 
                    source=iqr_cds, 
                    color="#AAAAAA", 
                    # alpha=0.5, 
                    line_color="black",
                    level="overlay"
                   )
    univar_fig.vbar("index", 0.5, "q1", "q2", 
                    source=iqr_cds, 
                    # alpha=0.5, 
                    color="#AAAAAA", 
                    level="overlay",
                    line_color="black")


    univar_fig.scatter(
        x=jitter('{}_jit'.format(f), 
                 width=0.45, 
                 range=univar_fig.x_range
                ),
        y=f, 
        source=geosource,
        alpha=0.5, size=5, 
        selection_color='orange',
        selection_line_width = 3,
        line_width = 1,
                    level="overlay",
        color="#1f7899",
        fill_alpha = 0.25,
        line_alpha = .85,
        nonselection_fill_alpha = 0.25,
        selection_fill_alpha = .75,

        )
    boxplot_figs.append(univar_fig)

show(row(*boxplot_figs))

In [52]:
# fill_color = {"field":geo_cmap_col, "transform": lx_cmap},
geo_fill_cb = """

"""

to_dropdown = Select(
    value="x",
    options=[("x", "Option X"), ("y", "Option Y")],
    visible=True,
    min_width=200,
    sizing_mode="stretch_width",
    styles=dict({"min-width": "120px"}),
    name="to_dropdown",
)

def cb_handler(attr, old, new):
    print("Previous label: " + old)
    print("Updated label: " + new)



to_dropdown.js_on_change("value", 
                         CustomJS(args=dict(
                             geo_source   = geosource,
                             main_source  = main_source,
                             geo_plot     = lx_plot,
                             hex_view     = bg_view,
                             hex_all      = AllIndices(),
                             hex_index    = IndexFilter(indices=[]),
                         ), code=geo_fill_cb)
                        )

show(row(lx_plot, scatter_plot, to_dropdown))


In [53]:
# fill_color = {"field":geo_cmap_col, "transform": lx_cmap},
geo_fill_cb = """
console.log(cb_obj)
console.log(dots)

dots.glyph.x['field'] = cb_obj.value + "_std"
dots.glyph.y['field'] = cb_obj.value + "_lag_std"
dots.glyph.fill_color['field'] = cb_obj.value + "_lisa_clust_filt"
dots.glyph.line_color['field'] = cb_obj.value + "_lisa_clust_filt"

console.log(scatter_plot)

scatter_plot.title.text = "Spatial Autocorrelation: " + cb_obj.value

scatter_xaxis[0].axis_label = cb_obj.value + "_std"
scatter_yaxis[0].axis_label = cb_obj.value + "_lag_std"

scatter_plot.change.emit()
dots.glyph.change.emit()
main_source.change.emit()
geo_source.change.emit()

console.log(main_source)
console.log(geo_source)
"""

to_dropdown = Select(
    value="PctBlack",
    options=[("PctBach", "Option X"), ("PctBlack", "Option Y")],
    visible=True,
    min_width=200,
    sizing_mode="stretch_width",
    styles=dict({"min-width": "120px"}),
    name="to_dropdown",
)

def cb_handler(attr, old, new):
    print("Previous label: " + old)
    print("Updated label: " + new)



to_dropdown.js_on_change("value", 
                         CustomJS(args=dict(
                             geo_source   = geosource,
                             main_source  = main_source,
                             geo_plot     = lx_plot,
                             hex_view     = bg_view,
                             hex_all      = AllIndices(),
                             hex_index    = IndexFilter(indices=[]),
                             dots         = scatter_dots,
                             scatter_plot = scatter_plot,
                             scatter_xaxis = scatter_plot.xaxis,
                             scatter_yaxis = scatter_plot.yaxis,
                             
                         ), code=geo_fill_cb)
                        )

show(row(scatter_plot, to_dropdown))


In [54]:
scatter_plot.select_one("scatter_dots")#.glyph.x = "PctBach"


GlyphRenderer(id='p1244', ...)

In [55]:
scatter_plot.select_one("scatter_dots").glyph.x = "PctBach"

In [56]:
show(row(lx_plot, scatter_plot, to_dropdown))


In [57]:
new_col = 'PctBach'
# new_col = 'PctRural'
new_col_x = new_col + '_std'
new_col_y = new_col + '_lag_std'
new_col_c = new_col + '_lisa_clust_filt'

pt_shapes.glyph.fill_color = {'field': new_col, 'transform': lx_cmap}

scatter_plot.title = "new_col: {}".format(new_col)

scatter_dots.glyph.x = new_col_x
scatter_dots.glyph.y = new_col_y
scatter_dots.glyph.fill_color = factor_cmap(new_col_c, 
                       palette=list(hilo_cmap.values()), 
                       factors=list(hilo_cmap.keys()))
scatter_dots.glyph.line_color = factor_cmap(new_col_c, 
                       palette=list(hilo_cmap.values()), 
                       factors=list(hilo_cmap.keys()))

new_lags_reg = linregress(lags_df[new_col_x], lags_df[new_col_y])

slope.gradient = new_lags_reg.slope


In [58]:
show(row(lx_plot, scatter_plot, to_dropdown))

In [59]:
main_source.data['umat_flat']

array([0.36985254, 0.38799017, 0.25614461, 0.2460512 , 0.16513448,
       0.26807346, 0.30919512, 0.31845109, 0.1989897 , 0.31216779,
       0.29459464, 0.40897501, 0.35963885, 0.3715303 , 0.29503389,
       0.32250934, 0.25381526, 0.31064963, 0.37336991, 0.33000083,
       0.23099848, 0.23012053, 0.34593157, 0.37086104, 0.26419392,
       0.26088311, 0.36968488, 0.27379233, 0.26479926, 0.24867494,
       0.37329156, 0.33123786, 0.2479272 , 0.23248402, 0.22997641,
       0.22806697, 0.2198028 , 0.28411488, 0.29929951, 0.21774054,
       0.22746645, 0.19970375, 0.27325935, 0.2956228 , 0.2676016 ,
       0.22543358, 0.18800833, 0.25729796, 0.3484451 , 0.33032598,
       0.23789901, 0.26530893, 0.2544815 , 0.2046031 , 0.26324198,
       0.27864645, 0.33772493, 0.19799879, 0.21697751, 0.22451216,
       0.42314171, 0.34705895, 0.30197223, 0.27929684, 0.21856465,
       0.27066047, 0.21609871, 0.3537108 , 0.24404367, 0.22152262,
       0.22988893, 0.21058748, 0.5373914 , 0.64294262, 0.42887

In [60]:
new_col = 'PctBach'
# new_col = 'PctRural'
new_col_x = new_col + '_std'
new_col_y = new_col + '_lag_std'
new_col_c = new_col + '_lisa_clust_filt'

scatter_dots.glyph = scatter_plot.circle(
    x=new_col_x, 
    y=new_col_y, 
    source=geosource,
    radius=0.05, 
    selection_line_color = "#2F2F2F",
    selection_line_width = 3,
    line_width = 1,
    fill_alpha = 0.75,
    nonselection_fill_alpha = 0.25,
    selection_fill_alpha = 1,

    color = factor_cmap(new_col_c, 
                       palette=list(hilo_cmap.values()), 
                       factors=list(hilo_cmap.keys()))
    
    ).glyph
show(row(lx_plot, scatter_plot, to_dropdown))


In [61]:
# # -*- coding: utf-8 -*-
# """
# Created on Fri Aug 19 14:28:52 2022

# @author: Gaelen
# """

# from bokeh.io import show, output_notebook
# from bokeh.models import ColumnDataSource, Select, Column, Row, CustomJS, PreText
# from bokeh.plotting import figure
# import pandas as pd
# # output_notebook()
# data = {'moo': [100, 200, 300, 100],
#         'woof': [200, 300, 100, 100],
#         'purr': [300, 100, 200, 200],
#         }
# df = pd.DataFrame(data)
# corr_mat = df.corr()
# source = ColumnDataSource(df)

# #make a second columndatasource of your correlation matrix result
# corr_source = ColumnDataSource(corr_mat)
# #if you look at this object's data attribute (i.e. drop this into the console):
#     # corr_source.data
# # you'll see that bokeh "translates" your df into a dictionary where the keys are column names, and the values correspond to arrays containing the column values
# # you'll also notice that bokeh makes an 'index' column storing the dataframe's index, which we can leverage



# test_all = AllIndices()
# test_view = CDSView(filter=test_all)

# p = figure(height=500, width=500, 
#            x_axis_label="moo", 
#            y_axis_label="woof",
#            tools='tap,reset,box_select',
           
        
#           )
# r = p.circle(x='moo', y='woof', 
#              radius=2,
#              source=source,
#              selection_fill_color='red',
#              nonselection_fill_color='green',
#             line_width = 1,
#             fill_alpha = 0.75,
#             nonselection_fill_alpha = 0.25,
#              view=test_view,
             
#             )
# selecty = Select(value='woof', title='y-axis', options=list(df.columns))
# selectx = Select(value='moo', title='x-axis', options=list(df.columns))


# cb = CustomJS(args=dict(r=r, p=p,
#                         selecty=selecty, 
#                         yaxis=p.yaxis, 
#                         xaxis=p.xaxis, 
#                         selectx=selectx,
#                         source=source,
#                         test_view    = test_view,
#                         test_all     = AllIndices(),
#                         test_index   = IndexFilter(indices=[]),
#                         q=q), 
#               code="""

#     const yf = selecty.value
#     const xf = selectx.value
# /*

#     r.glyph.y.field = yf;
#     r.glyph.x.field = xf;

#     yaxis[0].axis_label = yf
#     xaxis[0].axis_label = xf

#     r.glyph.change.emit()
#     // p.change.emit()
#     console.log('p=======')
#     console.log(r)
#     console.log(source.selected.indices)
#     console.log(test_view, test_index)
    
#     var selected = []
#     var indices = []
#     for (var i=0; i<source.get_length(); i++) {
#         indices.push(i)
        
        
#    }
# */
    
#     //test_index.indices = indices
#     //test_view.filter = test_index

#     //source.selected.indices = selected
#     //source.change.emit()

    
# r.glyph.y = {field: selecty.value};
#     //source.change.emit()

# """)

# selecty.js_on_change('value', cb)
# selectx.js_on_change('value', cb)


# s_cb = CustomJS(args=dict(r=r, p=p,
#                         selecty=selecty, 
#                         selectx=selectx,
#                         yaxis=p.yaxis, 
#                         xaxis=p.xaxis, 
#                         source=source,
#                         test_view    = test_view,
#                         test_all     = AllIndices(),
#                         test_index   = IndexFilter(indices=[]),
#                         q=q), 
#               code="""
# console.log(xaxis)
# console.log(selecty.value, selectx.value)
# console.log(cb_obj)
#     console.log(r)

# const yf = selecty.value
# const xf = selectx.value

# r.glyph.y.field = yf;
# r.glyph.x.field = xf;

# /*
# yaxis[0].axis_label = yf
# xaxis[0].axis_label = xf

# r.glyph.change.emit()
# source.change.emit()
# */


#               """)
# source.selected.js_on_change('indices', s_cb)

# show(Row(Column(selecty, selectx, q), p))

In [62]:
geosource.update

<bound method HasProps.update of GeoJSONDataSource(id='p1001', ...)>

In [63]:

from bokeh.layouts import column, row, gridplot, layout
from bokeh.models import ColumnDataSource, CDSView, CustomJS

from bokeh.models import ColumnDataSource, Select, HoverTool, Scatter
from bokeh.plotting import figure, show
from bokeh.sampledata.penguins import data as penguin_data
from bokeh.transform import factor_cmap
from bokeh.io import output_notebook, push_notebook, show
from bokeh.models.ranges    import DataRange1d

output_notebook()


Loading BokehJS ...

In [70]:

SPECIES = sorted(penguin_data.species.unique())

TOOLS = "box_select,tap,reset"

source = ColumnDataSource(penguin_data)
x1 = 'bill_depth_mm'
y1 = 'bill_length_mm'

left = figure(width=500, height=400, title=None, tools=TOOLS,
              background_fill_color="#fafafa")
left.scatter(x1, y1, source=source,
             color=factor_cmap('species', 'Category10_3', SPECIES))

right = figure(width=500, height=400, title=None, tools=TOOLS,
               # x_range=DataRange1d(bounds=(penguin_data[x1].min(), penguin_data[x1].max())),
               background_fill_color="#fafafa", y_axis_location="right")
rdots = right.scatter(x1, y1, source=source,
                      # fill_alpha=.75,
                      nonselection_fill_alpha=.5,
                      # selection_fill_alpha=.75,
                      # selection_alpha=.75,
                      name='rdots',
              fill_color=factor_cmap('species', 'Category10_3', SPECIES))

penguin_opts = ['bill_length_mm', 'bill_depth_mm',
       'flipper_length_mm', 'body_mass_g']

selectx = Select(value=x1, title='x-axis', options=penguin_opts)
selecty = Select(value=y1, title='y-axis', options=penguin_opts)

select_cb = """
const yf = selecty.value
const xf = selectx.value
rdots.glyph.y.field = yf;
rdots.glyph.x.field = xf;


rdots.change.emit();
source.change.emit();
"""
selectx.js_on_change('value', 
                     CustomJS(args=dict(
                         source=source,
                         rdots=rdots,
                         rfig=right,
                         selecty=selecty,
                         selectx=selectx
                     ), 
                              code=select_cb
                             ))

selecty.js_on_change('value', 
                     CustomJS(args=dict(
                         source=source,
                         rdots=rdots,
                         rfig=right,
                         selecty=selecty,
                         selectx=selectx
                     ), 
                              code=select_cb
                             ))

right.add_tools(HoverTool(renderers=[rdots]))
# right.x_range.renderers = [rdots]
# right.y_range.renderers = [rdots]

rdots_cb = """
console.log(cb_obj)
"""
source.selected.js_on_change('indices',
                    CustomJS(args=dict(
                        source=source,
                        rdots=rdots,
                        rfig=right,
                        selecty=selecty,
                        selectx=selectx),
                             code=rdots_cb
                            ))


selected_scatter = Scatter(fill_alpha=1, line_color='red')
nonselected_scatter = Scatter(fill_alpha=0.2)

# rdots.selection_glyph = selected_scatter
# rdots.nonselection_glyph = nonselected_scatter


show(row(column(selectx,selecty,row(right,left))))

In [65]:
right.x_range.bounds

In [66]:
print(penguin_data.columns)

penguin_data#.columns

Index(['species', 'island', 'bill_length_mm', 'bill_depth_mm',
       'flipper_length_mm', 'body_mass_g', 'sex'],
      dtype='object')


species     island  bill_length_mm  bill_depth_mm  flipper_length_mm  \
0    Adelie  Torgersen            39.1           18.7              181.0   
1    Adelie  Torgersen            39.5           17.4              186.0   
2    Adelie  Torgersen            40.3           18.0              195.0   
3    Adelie  Torgersen             NaN            NaN                NaN   
4    Adelie  Torgersen            36.7           19.3              193.0   
..      ...        ...             ...            ...                ...   
339  Gentoo     Biscoe             NaN            NaN                NaN   
340  Gentoo     Biscoe            46.8           14.3              215.0   
341  Gentoo     Biscoe            50.4           15.7              222.0   
342  Gentoo     Biscoe            45.2           14.8              212.0   
343  Gentoo     Biscoe            49.9           16.1              213.0   

     body_mass_g     sex  
0         3750.0    MALE  
1         3800.0  FEMALE  
2         3250.0  FEMALE  
3            NaN     NaN  
4         3450.0  FEMALE  
..           ...     ...  
339          NaN     NaN  
340       4850.0  FEMALE  
341       5750.0    MALE  
342       5200.0  FEMALE  
343       5400.0    MALE  

[344 rows x 7 columns]

In [67]:
from bokeh.models import ColumnDataSource, ColorPicker, CustomJS, Select
from bokeh.palettes import Bright6
from bokeh.plotting import figure, show
from bokeh.transform import factor_cmap
from bokeh.layouts import column, row

fruits = ['Apples', 'Pears', 'Nectarines', 'Plums', 'Grapes', 'Strawberries']
counts = [5, 3, 4, 2, 4, 6]

source = ColumnDataSource(data=dict(fruits=fruits, counts=counts))

p = figure(
    x_range = fruits, height = 350,
    toolbar_location = None,
    title = "Fruit Counts"
    )

r_vbar = p.vbar(
    x = 'fruits', top = 'counts', width=0.9,
    source = source, legend_field = "fruits",
    line_color = 'white',
    fill_color = factor_cmap('fruits', palette=Bright6, factors=fruits)
    )

p.xgrid.grid_line_color = None
p.y_range.start = 0
p.y_range.end = 9
p.legend.orientation = "horizontal"
p.legend.location = "top_center"

select = Select(
    title = 'Fruit',
    value = fruits[0],
    options = fruits
    )

color_picker = ColorPicker(
    title = 'Bar color specific fruit',
    color = r_vbar.glyph.fill_color.transform.palette[fruits.index(select.value)]
    )

# add callbacks to widgets
# update color picker with current color of selected fruit
select.js_on_change(
    "value",
    CustomJS(
        args = {
            'vbar': r_vbar,
            'color_picker': color_picker
        },
        code="""
          const idx = this.options.indexOf(this.value);
          const color = vbar.glyph.fill_color.transform.palette[idx];
          color_picker.color = color;
        """
    )
)

# update vbar color mapper
color_picker.js_on_change(
    'color',
    CustomJS(
        args = {
            'select': select,
            'vbar': r_vbar,
            'plot': p
        },
        code="""
          const idx = select.options.indexOf(select.value);
          const {transform} = vbar.glyph.fill_color;
          transform.palette[idx] = this.color;
          vbar.glyph.fill_color = {field: 'fruits', transform: transform};
          plot.reset.emit();
        """
    )
)

show(column(p, row(select, color_picker)))

In [68]:
from bokeh.layouts import layout
from bokeh.models import CategoricalColorMapper
from bokeh.models import ColumnDataSource
from bokeh.models.callbacks import CustomJS
from bokeh.models.widgets import CheckboxGroup
from bokeh.plotting import figure
from bokeh.plotting import show
from bokeh.transform import linear_cmap, transform

heatmap_color_palette = [
    '#0A3278',  # (10, 50, 120)
    '#0F4BA5',  # (15, 75, 165)
    '#1E6EC8',  # (30, 110, 200)
    '#3CA0F0',  # (60, 160, 240)
    '#50B4FA',  # (80, 180, 250)
    '#82D2FF',  # (130, 210, 255)
    '#A0F0FF',  # (160, 240, 255)
    '#FFE878',  # (255, 232, 120)
    '#FFC03C',  # (255, 192, 60)
    '#FFA000',  # (255, 160, 0)
    '#FF5F00',  # (255, 95, 0)
    '#FF3200',  # (255, 50, 0)
    '#E11400',  # (225, 20, 0)
    '#C00000',  # (192, 0, 0)
    '#A50000'  # (165, 0, 0)
]
circle_data = {
    'x': [1, 9, 4, 7, 2, 5, 3, 6],
    'y': [1, 9, 4, 7, 2, 5, 3, 6],
    'size': [9, 9, 6, 6, 9, 9, 6, 6],
    'desc': ['desc_1', 'desc_9', 'desc_4', 'desc_7', 'desc_2', 'desc_5', 'desc_3', 'desc_6'],
    'sensitivity': [2, 7, 9, 9, 1, 2, 8, 6]
}
color_mapper_from_sensitivity = linear_cmap('sensitivity', heatmap_color_palette, 0, 10)
color_mapper_from_desc = transform('desc', CategoricalColorMapper(
    factors=['desc_1', 'desc_9', 'desc_4', 'desc_7', 'desc_2', 'desc_5', 'desc_3', 'desc_6'],
    palette=['#330000', '#FF0000', '#FFFF00', '#00FF00', '#00FFFF', '#0000FF', '#7F00FF', '#FF007F']
))
p = figure(
    x_axis_type='datetime',
    width=800, height=800,
    background_fill_color='#DCDCDC', background_fill_alpha=0.4
)
circle_data_source = ColumnDataSource(circle_data)
circle_renderer = p.circle(
    x='x', y='y', size='size', source=circle_data_source,
    fill_color=color_mapper_from_desc,
    muted_alpha=0.2,
    line_color=None
)
callback = CustomJS(
    args=dict(renderer=circle_renderer,
              desc_cm=color_mapper_from_desc,
              sensitivity_cm=color_mapper_from_sensitivity),
    code="renderer.glyph.fill_color = this.active.length ? sensitivity_cm : desc_cm;"
)
checkbox_group = CheckboxGroup(labels=["Heat map"], active=[])
checkbox_group.js_on_change('active', callback)

show(layout([[checkbox_group], [p]]))

In [69]:
penguin_opts = ['bill_length_mm', 'bill_depth_mm',
       'flipper_length_mm', 'body_mass_g']
selectx = Select(value='bill_length_mm', title='x-axis', options=list(df.penguin_opts))
selecty = Select(value='body_mass_g', title='y-axis', options=list(df.penguin_opts))


NameError: name 'df' is not defined

In [ ]:
penguin_data['_current_x'] = penguin_data[penguin_opts[0]]
penguin_data['_current_y'] = penguin_data[penguin_opts[1]]

source = ColumnDataSource(penguin_data)

In [ ]:

SPECIES = sorted(penguin_data.species.unique())

TOOLS = "box_select,tap,reset"

x1 = penguin_opts[0]
y1 = penguin_opts[1]

selectx = Select(value=x1, title='x-axis', options=penguin_opts)
selecty = Select(value=y1, title='y-axis', options=penguin_opts)


left = figure(width=500, height=400, title=None, tools=TOOLS,
              background_fill_color="#fafafa")
left.scatter(x1, y1, source=source,
             color=factor_cmap('species', 'Category10_3', SPECIES))

right = figure(width=500, height=400, title=None, tools=TOOLS,
               background_fill_color="#fafafa", y_axis_location="right")
rdots = right.scatter('_current_x', '_current_y',
                      source=source,
                      fill_alpha=.75,
                      size=5,
                      nonselection_fill_alpha=.25,
                      selection_fill_alpha=.75,
                      name='rdots',
              fill_color=factor_cmap('species', 'Category10_3', SPECIES))


selected_scatter = Scatter(fill_alpha=1, line_color='red')
nonselected_scatter = Scatter(fill_alpha=0.2, line_color='red')

# rdots.selection_glyph = selected_scatter
# rdots.nonselection_glyph = nonselected_scatter


select_cb = """
const yf = selecty.value
const xf = selectx.value

console.log(yf, xf)
console.log(source)
//rdots.glyph.y.field = yf;
//rdots.glyph.x.field = xf;

source.data['_current_x'] = source.data[xf]
source.data['_current_y'] = source.data[yf]

//rdots.change.emit();
source.change.emit();

"""
selectx.js_on_change('value', 
                     CustomJS(args=dict(
                         source=source,
                         rdots=rdots,
                         rfig=right,
                         selecty=selecty,
                         selectx=selectx
                     ), 
                              code=select_cb
                             ))

selecty.js_on_change('value', 
                     CustomJS(args=dict(
                         source=source,
                         rdots=rdots,
                         rfig=right,
                         selecty=selecty,
                         selectx=selectx
                     ), 
                              code=select_cb
                             ))

right.add_tools(HoverTool(renderers=[rdots]))
# right.x_range.renderers = [rdots]
# right.y_range.renderers = [rdots]

rdots_cb = """
console.log(cb_obj)
"""
source.selected.js_on_change('indices',
                    CustomJS(args=dict(
                        source=source,
                        rdots=rdots,
                        rfig=right,
                        selecty=selecty,
                        selectx=selectx),
                             code=rdots_cb
                            ))


show(row(column(selectx,selecty,row(right,left))))